In [25]:
import os
import json

os.environ["CUDA_VISIBLE_DEVICES"] = "0"

%pip install nltk
%pip install git+https://github.com/suno-ai/bark.git

from IPython.display import Audio
import nltk  # we'll use this to split into sentences
import numpy as np

from bark.generation import (
    generate_text_semantic,
    preload_models,
)
from bark.api import semantic_to_waveform
from bark import generate_audio, SAMPLE_RATE

Defaulting to user installation because normal site-packages is not writeable

[notice] A new release of pip is available: 23.1 -> 23.1.2
[notice] To update, run: python3 -m pip install --upgrade pip
Note: you may need to restart the kernel to use updated packages.
Defaulting to user installation because normal site-packages is not writeable
  Cloning https://github.com/suno-ai/bark.git to /tmp/pip-req-build-jk0fwbhb
  Running command git clone --filter=blob:none --quiet https://github.com/suno-ai/bark.git /tmp/pip-req-build-jk0fwbhb
  Resolved https://github.com/suno-ai/bark.git to commit 1ad007171e0c46078eb6d3afb6db4daf0c4f41cd
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Installing backend dependencies ... done
  Preparing metadata (pyproject.toml) ... done

[notice] A new release of pip is available: 23.1 -> 23.1.2
[notice] To update, run: python3 -m pip install --upgrade pip
Note: you may need to restart the kernel to use updated packag

In [26]:
preload_models()

# Simple Long-Form Generation
We split longer text into sentences using `nltk` and generate the sentences one by one.

In [27]:
script = """
Player Two is great, actually amazing. But do you know what's greater? 
You.
""".replace("\n", " ").strip()

In [19]:
nltk.download('punkt')
sentences = nltk.sent_tokenize(script)

[nltk_data] Downloading package punkt to /home/ubuntu/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


In [30]:
SPEAKER = "v2/en_speaker_1"
silence = np.zeros(int(0.25 * SAMPLE_RATE))  # quarter second of silence
print('sample rate', SAMPLE_RATE)
pieces = []
piecesJSON = []
for sentence in sentences:
    audio_array = generate_audio(sentence, history_prompt=SPEAKER)
    pieces += [audio_array, silence.copy()]
    piecesJSON += [audio_array.tolist(), silence.copy().tolist()]
    print('done', sentence, pieces)
    
with open('readme.txt', 'w') as f:
    json.dump(piecesJSON, f)


sample rate 24000


100%|██████████| 9/9 [00:04<00:00,  2.04it/s]


done Player Two is great, actually amazing. [array([2.7518435e-03, 1.9405491e-03, 1.8355843e-03, ..., 1.7460785e-05,
       2.8498689e-05, 3.5446094e-05], dtype=float32), array([0., 0., 0., ..., 0., 0., 0.])]


100%|██████████| 7/7 [00:03<00:00,  1.85it/s]


done But do you know what's greater? [array([2.7518435e-03, 1.9405491e-03, 1.8355843e-03, ..., 1.7460785e-05,
       2.8498689e-05, 3.5446094e-05], dtype=float32), array([0., 0., 0., ..., 0., 0., 0.]), array([ 7.2604197e-04,  3.0385063e-04,  1.1204043e-05, ...,
       -1.1618856e-02, -1.3461938e-02, -1.5023532e-02], dtype=float32), array([0., 0., 0., ..., 0., 0., 0.])]


100%|██████████| 5/5 [00:02<00:00,  2.22it/s]


done You. [array([2.7518435e-03, 1.9405491e-03, 1.8355843e-03, ..., 1.7460785e-05,
       2.8498689e-05, 3.5446094e-05], dtype=float32), array([0., 0., 0., ..., 0., 0., 0.]), array([ 7.2604197e-04,  3.0385063e-04,  1.1204043e-05, ...,
       -1.1618856e-02, -1.3461938e-02, -1.5023532e-02], dtype=float32), array([0., 0., 0., ..., 0., 0., 0.]), array([7.8580005e-04, 3.8324567e-04, 5.2869145e-05, ..., 7.7883707e-04,
       8.1215403e-04, 8.3577598e-04], dtype=float32), array([0., 0., 0., ..., 0., 0., 0.])]


In [ ]:
Audio(np.concatenate(pieces), rate=SAMPLE_RATE)

# $ \\ $

# Advanced Long-Form Generation
Somtimes Bark will hallucinate a little extra audio at the end of the prompt.
We can solve this issue by lowering the threshold for bark to stop generating text. 
We use the `min_eos_p` kwarg in `generate_text_semantic`

In [28]:
GEN_TEMP = 0.6
SPEAKER = "v2/en_speaker_9"
silence = np.zeros(int(0.25 * SAMPLE_RATE))  # quarter second of silence

pieces = []
for sentence in sentences:
    semantic_tokens = generate_text_semantic(
        sentence,
        history_prompt=SPEAKER,
        temp=GEN_TEMP,
        min_eos_p=0.05,  # this controls how likely the generation is to end
    )

    audio_array = semantic_to_waveform(semantic_tokens, history_prompt=SPEAKER,)
    pieces += [audio_array, silence.copy()]



100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 7/7 [00:03<00:00,  1.85it/s]


In [29]:
Audio(np.concatenate(pieces), rate=SAMPLE_RATE)

# $ \\ $

# Make a Long-Form Dialog with Bark

### Step 1: Format a script and speaker lookup

In [38]:
speaker_lookup = {"Samantha": "v2/en_speaker_9", "John": "v2/en_speaker_2"}

# Script generated by chat GPT
script = """
Samantha: Hey, have you heard about this new text-to-audio model called "Bark"?

John: No, I haven't. What's so special about it?

Samantha: Well, apparently it's the most realistic and natural-sounding text-to-audio model out there right now. People are saying it sounds just like a real person speaking.

John: Wow, that sounds amazing. How does it work?

Samantha: I think it uses advanced machine learning algorithms to analyze and understand the nuances of human speech, and then replicates those nuances in its own speech output.

John: That's pretty impressive. Do you think it could be used for things like audiobooks or podcasts?

Samantha: Definitely! In fact, I heard that some publishers are already starting to use Bark to create audiobooks. And I bet it would be great for podcasts too.

John: I can imagine. It would be like having your own personal voiceover artist.

Samantha: Exactly! I think Bark is going to be a game-changer in the world of text-to-audio technology."""
script = script.strip().split("\n")
script = [s.strip() for s in script if s]
script

['Samantha: Hey, have you heard about this new text-to-audio model called "Bark"?',
 "John: No, I haven't. What's so special about it?",
 "Samantha: Well, apparently it's the most realistic and natural-sounding text-to-audio model out there right now. People are saying it sounds just like a real person speaking.",
 'John: Wow, that sounds amazing. How does it work?',
 'Samantha: I think it uses advanced machine learning algorithms to analyze and understand the nuances of human speech, and then replicates those nuances in its own speech output.',
 "John: That's pretty impressive. Do you think it could be used for things like audiobooks or podcasts?",
 'Samantha: Definitely! In fact, I heard that some publishers are already starting to use Bark to create audiobooks. And I bet it would be great for podcasts too.',
 'John: I can imagine. It would be like having your own personal voiceover artist.',
 'Samantha: Exactly! I think Bark is going to be a game-changer in the world of text-to-audi

### Step 2: Generate the audio for every speaker turn

In [39]:
pieces = []
silence = np.zeros(int(0.5*SAMPLE_RATE))
for line in script:
    speaker, text = line.split(": ")
    audio_array = generate_audio(text, history_prompt=speaker_lookup[speaker], )
    pieces += [audio_array, silence.copy()]

100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 20/20 [00:10<00:00,  1.82it/s]


### Step 3: Concatenate all of the audio and play it

In [40]:
Audio(np.concatenate(pieces), rate=SAMPLE_RATE)